In [3]:
import pandas as pd
import Go_tools

In [4]:
arabi_go_matrix = pd.read_csv(
    "/Users/michael/Data/Reference_data/Arabdidopsis_go_matrix_from_tair_gaf.csv",
    index_col=0,
)
arabi_go_matrix
defense_terms = pd.read_csv(
    "/Users/michael/Data/Luke_terrace_experiment/General_data/Defense_go_terms.csv"
)
defense_terms

GO Term ID                                GO Term Descripton   \
0   GO:0012501                              programmed cell death   
1   GO:0009626                 Plant type hypersensitive response   
2   GO:0042742                      defense response to bacterium   
3   GO:0071219  cellular response to molecule of bacterial origin   
4   GO:0045087                             innate immune response   
5   GO:0009862  systemic acquired resistance, salicylic acid m...   
6   GO:0009861  jasmonic acid and ethylene-dependent systemic ...   
7   GO:0034055  effector-mediated activation of host programme...   
8   GO:0009682                        induced systemic resistance   
9   GO:0009626                 plant-type hypersensitive response   
10  GO:0009627                       systemic acquired resistance   
11  GO:0002237           response to molecule of bacterial origin   
12  GO:0012501                              programmed cell death   
13  GO:0010421   hydrogen peroxide-mediated programmed cell death   

                Note  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN  
5                NaN  
6                NaN  
7   not enough genes  
8                NaN  
9                NaN  
10               NaN  
11               NaN  
12               NaN  
13               NaN

In [5]:
gene_list = [
    "AT1G02920",
    "AT1G02930",
    "AT1G21110",
    "AT1G21120",
    "AT1G26380",
    "AT1G26410",
    "AT1G26420",
    "AT1G35230",
    "AT1G64170",
    "AT1G65500",
    "AT1G76930",
    "AT2G19190",
    "AT2G25470",
    "AT2G30750",
    "AT2G39200",
    "AT2G43620",
    "AT3G46280",
    "AT4G12490",
    "AT4G12500",
    "AT4G23140",
    "AT4G23220",
    "AT4G28420",
    "AT5G24110",
    "AT5G64120",
]

In [9]:
defense_terms.loc[14] = [
    "GO:Luke Custom",
    "General Non Self Recognition Genes",
    "Custom From Luke",
]
defense_terms

GO Term ID                                GO Term Descripton   \
0       GO:0012501                              programmed cell death   
1       GO:0009626                 Plant type hypersensitive response   
2       GO:0042742                      defense response to bacterium   
3       GO:0071219  cellular response to molecule of bacterial origin   
4       GO:0045087                             innate immune response   
5       GO:0009862  systemic acquired resistance, salicylic acid m...   
6       GO:0009861  jasmonic acid and ethylene-dependent systemic ...   
7       GO:0034055  effector-mediated activation of host programme...   
8       GO:0009682                        induced systemic resistance   
9       GO:0009626                 plant-type hypersensitive response   
10      GO:0009627                       systemic acquired resistance   
11      GO:0002237           response to molecule of bacterial origin   
12      GO:0012501                              programmed cell death   
13      GO:0010421   hydrogen peroxide-mediated programmed cell death   
14  GO:Luke Custom                 General Non Self Recognition Genes   

                Note  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN  
5                NaN  
6                NaN  
7   not enough genes  
8                NaN  
9                NaN  
10               NaN  
11               NaN  
12               NaN  
13               NaN  
14  Custom From Luke

In [11]:
arabi_go_matrix["GO:Luke Custom"] = 0
arabi_go_matrix.loc[gene_list, "GO:Luke Custom"] = 1
arabi_go_matrix.sum()

GO:0000001         1.0
GO:0000009         1.0
GO:0000012         2.0
GO:0000014         6.0
GO:0000023         2.0
                  ... 
GO:2001227         2.0
GO:2001280         2.0
GO:2001289        10.0
GO:2001294         1.0
GO:Luke Custom    24.0
Length: 6056, dtype: float64

In [13]:
# Extract unique GO terms from defense_terms
go_terms = defense_terms["GO Term ID"].unique()
print(f"Found {len(go_terms)} unique GO terms")
print(go_terms)

Found 13 unique GO terms
['GO:0012501' 'GO:0009626' 'GO:0042742' 'GO:0071219' 'GO:0045087'
 'GO:0009862' 'GO:0009861' 'GO:0034055' 'GO:0009682' 'GO:0009627'
 'GO:0002237' 'GO:0010421' 'GO:Luke Custom']


In [14]:
from itertools import combinations

# Create a dictionary mapping GO terms to their genes
go_to_genes = {}
for go_term in go_terms:
    # Get genes that have this GO term (columns with value 1)
    genes = arabi_go_matrix[arabi_go_matrix[go_term] == 1].index.tolist()
    go_to_genes[go_term] = set(genes)
    print(f"{go_term}: {len(genes)} genes")

print(f"\nTotal GO terms: {len(go_to_genes)}")

# Generate all possible combinations of GO terms
# Get all combinations of different sizes
all_combinations = {}
for r in range(1, len(go_terms) + 1):
    for combo in combinations(go_terms, r):
        # Find union of genes for this combination
        gene_sets = [go_to_genes[term] for term in combo]
        combined_genes = set.union(*gene_sets)
        combo_key = " OR ".join(combo)
        all_combinations[combo_key] = combined_genes

# Filter to only keep combinations with more than 20 genes
filtered_combinations = {k: v for k, v in all_combinations.items() if len(v) > 20}

print(f"\nGenerated {len(all_combinations)} combinations")
print(f"Filtered to {len(filtered_combinations)} combinations with >20 genes")
print("\nCombinations with gene counts:")
for combo_key, genes in sorted(
    filtered_combinations.items(), key=lambda x: len(x[1]), reverse=True
):
    print(f"  {combo_key}: {len(genes)} genes")

GO:0012501: 34 genes
GO:0009626: 54 genes
GO:0042742: 325 genes
GO:0071219: 7 genes
GO:0045087: 58 genes
GO:0009862: 16 genes
GO:0009861: 11 genes
GO:0034055: 1 genes
GO:0009682: 21 genes
GO:0009627: 57 genes
GO:0002237: 41 genes
GO:0010421: 2 genes
GO:Luke Custom: 24 genes

Total GO terms: 13

Generated 8191 combinations
Filtered to 8173 combinations with >20 genes

Combinations with gene counts:
  GO:0012501 OR GO:0009626 OR GO:0042742 OR GO:0071219 OR GO:0045087 OR GO:0009862 OR GO:0009861 OR GO:0034055 OR GO:0009682 OR GO:0009627 OR GO:0002237 OR GO:0010421 OR GO:Luke Custom: 520 genes
  GO:0012501 OR GO:0009626 OR GO:0042742 OR GO:0071219 OR GO:0045087 OR GO:0009862 OR GO:0009861 OR GO:0034055 OR GO:0009682 OR GO:0009627 OR GO:0002237 OR GO:Luke Custom: 519 genes
  GO:0012501 OR GO:0009626 OR GO:0042742 OR GO:0071219 OR GO:0045087 OR GO:0009862 OR GO:0009861 OR GO:0009682 OR GO:0009627 OR GO:0002237 OR GO:0010421 OR GO:Luke Custom: 519 genes
  GO:0012501 OR GO:0009626 OR GO:004274

In [15]:
filtered_combinations

{'GO:0012501': {'AT1G08720',
  'AT1G12220',
  'AT1G13680',
  'AT1G16420',
  'AT1G26630',
  'AT1G29690',
  'AT1G29850',
  'AT1G32230',
  'AT1G64280',
  'AT1G73260',
  'AT2G19860',
  'AT2G26560',
  'AT2G36010',
  'AT2G38530',
  'AT2G41060',
  'AT3G06490',
  'AT3G15010',
  'AT3G16770',
  'AT3G20210',
  'AT3G27060',
  'AT3G44880',
  'AT3G45860',
  'AT3G50930',
  'AT3G56860',
  'AT4G23130',
  'AT4G23170',
  'AT4G23280',
  'AT4G29130',
  'AT4G35790',
  'AT4G38360',
  'AT5G02190',
  'AT5G10380',
  'AT5G43940',
  'AT5G51290'},
 'GO:0009626': {'AT1G02860',
  'AT1G08450',
  'AT1G12220',
  'AT1G19250',
  'AT1G28380',
  'AT1G29340',
  'AT1G29690',
  'AT1G59870',
  'AT1G71220',
  'AT2G13790',
  'AT2G20310',
  'AT2G26560',
  'AT3G07040',
  'AT3G20600',
  'AT3G21220',
  'AT3G25070',
  'AT3G28910',
  'AT3G44670',
  'AT3G46530',
  'AT3G48090',
  'AT3G50930',
  'AT3G52430',
  'AT3G54420',
  'AT3G55830',
  'AT4G02640',
  'AT4G03110',
  'AT4G12720',
  'AT4G19660',
  'AT4G20380',
  'AT4G23210',
  'AT4G2609

In [16]:
transcriptome = pd.read_csv(
    "/Users/michael/Data/Luke_terrace_experiment/General_data/plate1_4_tpm_normalized.csv",
    index_col=0,
)
rows_to_drop_expression_data = [
    "A2450525897_n01_undetermined",
    "A2449446903_n01_undetermined",
    "B250508004_n01_undetermined",
    "B2449500127_n01_undetermined",
]
transcriptome = transcriptome.drop(index=rows_to_drop_expression_data)
transcriptome = transcriptome.sort_index()

In [17]:
metadata = pd.read_csv(
    "/Users/michael/Data/Luke_terrace_experiment/General_data/Plates_1_to_4_metadata_merged_luke.csv",
    index_col=0,
)
metadata = metadata.drop(
    columns=[
        "arb.sort",
        "sample-id",
        "Ambiguous Unstranded",
        "Ambiguous Forward",
        "Multimapping",
        "Unmapped Over Mapped",
    ]
)
metadata["Date and Time"] = metadata["date"] + " " + metadata["time"]
luke_time_data_format = "%-m/%-d/%y %-H:%-M"
metadata["Date and Time"] = pd.to_datetime(
    metadata["Date and Time"], format=luke_time_data_format
)


unusable_samples = [
    "A2450525897_n01_LICRNA01_A06",
    "A2450525897_n01_LICRNA01_A08",
    "A2450525897_n01_LICRNA01_C11",
    "A2450525897_n01_LICRNA01_D11",
    "A2450525897_n01_LICRNA01_D12",
    "A2449446903_n01_LICRNA02_F01",
    "B2449500127_n01_LICRNA04_A04",
    "B2449500127_n01_LICRNA04_A06",
    "B2449500127_n01_LICRNA04_A07",
]
borderline_unusable = [
    "A2450525897_n01_LICRNA01_F03",
    "A2450525897_n01_LICRNA01_G07",
    "A2449446903_n01_LICRNA02_A04",
    "A2449446903_n01_LICRNA02_H10",
    "B2449500127_n01_LICRNA04_H02",
    "B2449500127_n01_LICRNA04_H11",
]
all_unsable = borderline_unusable + unusable_samples

In [18]:
trimmed_transcriptome = transcriptome.drop(index=all_unsable)
trimmed_metadata = metadata.drop(index=all_unsable)
long_term_transcriptome = trimmed_transcriptome.loc[
    trimmed_metadata["Experiment Type"] == "Long Term"
]
long_term_metadata = trimmed_metadata.loc[
    trimmed_metadata["Experiment Type"] == "Long Term"
]

In [19]:
microbiome_abundance = pd.read_csv(
    "/Users/michael/Data/Luke_terrace_experiment/Microbiome/lic2024_16S_rab.csv"
)
long_term_microbiome = microbiome_abundance.merge(
    metadata[["sampID", "Experiment Type"]], left_on="plantID", right_on="sampID"
)
long_term_microbiome = long_term_microbiome.loc[
    long_term_microbiome["Experiment Type"] == "Long Term"
]
long_term_microbiome

Sample sample.type timepoint      date  time platename  daysincestart  \
1      LIC063       plant       t06  11/28/23  8:00    LIC_01             27   
2      LIC159       plant       t14   1/23/24  8:00    LIC_02             83   
4      LIC306       plant       t26    3/8/24  8:00    LIC_04            128   
5      LIC016       plant       t02   11/7/23  8:00    LIC_01              6   
9      LIC051       plant       t05  11/21/23  8:00    LIC_01             20   
...       ...         ...       ...       ...   ...       ...            ...   
12278  LIC157       plant       t14   1/23/24  8:00    LIC_02             83   
12280  LIC195       plant       t17    2/2/24  8:00    LIC_03             93   
12281  LIC122       plant       t11  12/15/23  8:00    LIC_02             44   
12282  LIC028       plant       t03  11/14/23  8:00    LIC_01             13   
12285  LIC230       plant       t20   2/16/24  8:00    LIC_03            107   

      plantID      Kingdom           Phylum                Class  \
1      LIC063  d__Bacteria   Pseudomonadota  Alphaproteobacteria   
2      LIC159  d__Bacteria  Cyanobacteriota       Cyanobacteriia   
4      LIC306  d__Bacteria   Pseudomonadota  Alphaproteobacteria   
5      LIC016  d__Bacteria   Pseudomonadota  Alphaproteobacteria   
9      LIC051  d__Bacteria   Pseudomonadota  Alphaproteobacteria   
...       ...          ...              ...                  ...   
12278  LIC157  d__Bacteria   Actinomycetota        Actinomycetes   
12280  LIC195  d__Bacteria   Actinomycetota        Actinomycetes   
12281  LIC122  d__Bacteria   Actinomycetota        Actinomycetes   
12282  LIC028  d__Bacteria   Actinomycetota        Actinomycetes   
12285  LIC230  d__Bacteria   Pseudomonadota  Alphaproteobacteria   

                     Order                    Family                  Genus  \
1         Sphingomonadales  Sphingomonadaceae_486827  Sphingomonas_L_486704   
2         Cyanobacteriales        Coleofasciculaceae                Caldora   
4         Sphingomonadales  Sphingomonadaceae_486827  Sphingomonas_L_486704   
5         Sphingomonadales  Sphingomonadaceae_486827  Sphingomonas_L_486704   
9       Rhizobiales_505101              Rhizobiaceae    Neorhizobium_500197   
...                    ...                       ...                    ...   
12278  Propionibacteriales      Propionibacteriaceae         Friedmanniella   
12280  Propionibacteriales      Propionibacteriaceae         Friedmanniella   
12281  Propionibacteriales           Nocardioidaceae  Nocardioides_A_392796   
12282      Mycobacteriales       Geodermatophilaceae          Modestobacter   
12285   Rhizobiales_505101          Beijerinckiaceae       Methylobacterium   

                                  Species  AbundR100  sampID Experiment Type  
1       Sphingomonas_L_486704 sp000786205       66.1  LIC063       Long Term  
2                     Caldora sp010672925       60.5  LIC159       Long Term  
4       Sphingomonas_L_486704 sp000786205       57.2  LIC306       Long Term  
5       Sphingomonas_L_486704 sp000786205       54.4  LIC016       Long Term  
9                       Neorhizobium soli       49.7  LIC051       Long Term  
...                                   ...        ...     ...             ...  
12278              Friedmanniella luteola        0.5  LIC157       Long Term  
12280                Friedmanniella flava        0.5  LIC195       Long Term  
12281  Nocardioides_A_392796 hankookensis        0.5  LIC122       Long Term  
12282               Modestobacter muralis        0.5  LIC028       Long Term  
12285        Methylobacterium sp001424705        0.5  LIC230       Long Term  

[7379 rows x 18 columns]

In [20]:
genus_sum = (
    long_term_microbiome[["Sample", "Genus", "AbundR100"]]
    .groupby(["Sample", "Genus"])
    .sum()
)
genus_sum = genus_sum.reset_index()

genus_sum_w_tp = genus_sum.merge(
    metadata[["sampID", "timepoint"]], left_on="Sample", right_on="sampID"
)
genus_sum_w_tp

Sample                   Genus  AbundR100  sampID timepoint
0     LIC001       Actinomycetospora        0.6  LIC001       t01
1     LIC001            Actinoplanes        1.1  LIC001       t01
2     LIC001           Aeromicrobium        0.8  LIC001       t01
3     LIC001            Blastococcus        1.7  LIC001       t01
4     LIC001      Caulobacter_487784        0.5  LIC001       t01
...      ...                     ...        ...     ...       ...
5098  LIC368  Pseudoduganella_570666        0.5  LIC368       t08
5099  LIC368    Pseudomonas_E_647464        2.6  LIC368       t08
5100  LIC368            Rhodoferax_C        6.6  LIC368       t08
5101  LIC368   Sphingomonas_L_486704       19.7  LIC368       t08
5102  LIC368              Variovorax        1.3  LIC368       t08

[5103 rows x 5 columns]

In [21]:
all_present_genus = genus_sum_w_tp["Genus"].unique()
all_present_genus

array(['Actinomycetospora', 'Actinoplanes', 'Aeromicrobium',
       'Blastococcus', 'Caulobacter_487784', 'Chryseobacterium_A_796612',
       'Curtobacterium', 'Dactylopiibacterium', 'Flavobacterium',
       'Friedmanniella', 'Frigoribacterium', 'Geodermatophilus',
       'Herbaspirillum', 'Hylemonella', 'Kineococcus', 'Kineosporia',
       'Klenkia', 'Kordiimonas', 'Massilia_574544', 'Methylobacterium',
       'Methylophilus', 'Microbacterium_A_383321', 'Nakamurella',
       'Neorhizobium_500197', 'Nocardioides_A_392796',
       'Pseudoduganella_570666', 'Pseudomonas_B_650453',
       'Pseudomonas_E_647464', 'Pseudomonas_E_647626', 'Rhodoferax_C',
       'Solirubrobacter', 'Sphingomonas_L_486704', 'Telluria_573210',
       'Variovorax', 'Arthrobacter_E_385446', 'Arthrobacter_E_385777',
       'Caballeronia', 'Marmoricola_A_392027', 'Massilia_574424',
       'Microlunatus_B', 'Nocardioides_A_392805',
       'Noviherbaspirillum_A_568106', 'Paucimonas', 'Pedococcus',
       'Pseudodugane

In [22]:
## Need to fill in missing genus in every sample first
for sampID in genus_sum_w_tp["sampID"].unique():
    sampid_only_df = genus_sum_w_tp.loc[genus_sum_w_tp["sampID"] == sampID]
    present_genus_in_samp = sampid_only_df["Genus"].unique()
    difference_in_present_bacteria = list(
        set(all_present_genus) - set(present_genus_in_samp)
    )
    current_time_point = sampid_only_df["timepoint"].iloc[0]
    empty_df_to_add = pd.DataFrame(
        columns=["Sample", "Genus", "AbundR100", "sampID", "timepoint"]
    )
    empty_df_to_add["Genus"] = difference_in_present_bacteria
    empty_df_to_add["Sample"] = sampID
    empty_df_to_add["AbundR100"] = 0
    empty_df_to_add["sampID"] = sampID
    empty_df_to_add["timepoint"] = current_time_point
    genus_sum_w_tp = pd.concat([genus_sum_w_tp, empty_df_to_add])

In [23]:
genus_sum_w_tp

Sample                 Genus  AbundR100  sampID timepoint
0    LIC001     Actinomycetospora        0.6  LIC001       t01
1    LIC001          Actinoplanes        1.1  LIC001       t01
2    LIC001         Aeromicrobium        0.8  LIC001       t01
3    LIC001          Blastococcus        1.7  LIC001       t01
4    LIC001    Caulobacter_487784        0.5  LIC001       t01
..      ...                   ...        ...     ...       ...
109  LIC368               Inhella        0.0  LIC368       t08
110  LIC368      Duganella_570917        0.0  LIC368       t08
111  LIC368          Williamsia_A        0.0  LIC368       t08
112  LIC368  Herminiimonas_567389        0.0  LIC368       t08
113  LIC368       Gryllotalpicola        0.0  LIC368       t08

[30414 rows x 5 columns]

In [24]:
from scipy.stats import pearsonr, spearmanr

# Get Pseudomonas_E_647626 abundance for each sample (using 'Sample' which has LIC IDs)
pseudomonas_data = genus_sum_w_tp[genus_sum_w_tp["Genus"] == "Pseudomonas_E_647626"]
pseudomonas_abundance = pseudomonas_data.set_index("Sample")["AbundR100"]

# Get the mapping from filename to sampID (LIC IDs) from metadata
# We need samples that have both transcriptome data and Pseudomonas abundance
common_lic_ids = list(
    set(long_term_metadata["sampID"]) & set(pseudomonas_abundance.index)
)
common_filenames = long_term_metadata[
    long_term_metadata["sampID"].isin(common_lic_ids)
].index.tolist()

# Also filter to only those that are in the transcriptome
common_filenames = [f for f in common_filenames if f in long_term_transcriptome.index]

print(
    f"Found {len(common_filenames)} samples in common between transcriptome and microbiome data"
)

# Calculate correlation for each gene set combination
correlation_results = []

for combo_name, gene_set in filtered_combinations.items():
    # Get genes that are actually in the transcriptome
    genes_in_data = list(set(gene_set) & set(long_term_transcriptome.columns))

    if len(genes_in_data) == 0:
        continue

    # Calculate mean expression for these genes in each sample (using filename index)
    mean_expression = long_term_transcriptome.loc[common_filenames, genes_in_data].mean(
        axis=1
    )

    # Get corresponding Pseudomonas abundance (need to map filename to LIC ID)
    lic_ids = long_term_metadata.loc[common_filenames, "sampID"]
    pseudo_abund = pseudomonas_abundance.loc[lic_ids].values

    # Calculate correlations
    pearson_corr, pearson_pval = pearsonr(mean_expression.values, pseudo_abund)
    spearman_corr, spearman_pval = spearmanr(mean_expression.values, pseudo_abund)

    correlation_results.append(
        {
            "combination": combo_name,
            "n_genes_total": len(gene_set),
            "n_genes_in_data": len(genes_in_data),
            "pearson_r": pearson_corr,
            "pearson_pval": pearson_pval,
            "spearman_r": spearman_corr,
            "spearman_pval": spearman_pval,
        }
    )

# Convert to DataFrame and sort by absolute Pearson correlation
correlation_df = pd.DataFrame(correlation_results)
correlation_df["abs_pearson"] = correlation_df["pearson_r"].abs()
correlation_df = correlation_df.sort_values("abs_pearson", ascending=False)

print(f"\nAnalyzed {len(correlation_df)} gene set combinations")
print("\nTop 20 combinations by absolute Pearson correlation:")
print(correlation_df.head(20).to_string())

Found 214 samples in common between transcriptome and microbiome data

Analyzed 8173 gene set combinations

Top 20 combinations by absolute Pearson correlation:
                                                             combination  n_genes_total  n_genes_in_data  pearson_r  pearson_pval  spearman_r  spearman_pval  abs_pearson
0                                                             GO:0012501             34               34   0.223913      0.000973    0.219758       0.001214     0.223913
14                                              GO:0012501 OR GO:0034055             35               35   0.223692      0.000984    0.220402       0.001173     0.223692
18                                              GO:0012501 OR GO:0010421             35               35   0.222452      0.001052    0.219074       0.001258     0.222452
132                               GO:0012501 OR GO:0034055 OR GO:0010421             36               36   0.222235      0.001064    0.219719       0.001216   

In [27]:
correlation_df

combination  n_genes_total  n_genes_in_data  \
0                                GO:0012501             34               34   
14                 GO:0012501 OR GO:0034055             35               35   
18                 GO:0012501 OR GO:0010421             35               35   
132  GO:0012501 OR GO:0034055 OR GO:0010421             36               36   
10                 GO:0012501 OR GO:0071219             41               41   
..                                      ...            ...              ...   
53                 GO:0045087 OR GO:0010421             60               60   
64                 GO:0034055 OR GO:0009682             22               22   
4                                GO:0009682             21               21   
341  GO:0034055 OR GO:0009682 OR GO:0010421             24               24   
70                 GO:0009682 OR GO:0010421             23               23   

     pearson_r  pearson_pval  spearman_r  spearman_pval  abs_pearson  
0     0.223913      0.000973    0.219758       0.001214     0.223913  
14    0.223692      0.000984    0.220402       0.001173     0.223692  
18    0.222452      0.001052    0.219074       0.001258     0.222452  
132   0.222235      0.001064    0.219719       0.001216     0.222235  
10    0.220203      0.001186    0.220550       0.001164     0.220203  
..         ...           ...         ...            ...          ...  
53    0.003205      0.962820    0.025520       0.710486     0.003205  
64    0.003154      0.963410    0.034466       0.616100     0.003154  
4     0.003012      0.965056    0.035391       0.606650     0.003012  
341   0.002785      0.967695    0.034166       0.619178     0.002785  
70    0.002644      0.969333    0.034124       0.619603     0.002644  

[8173 rows x 8 columns]

In [25]:
# Save top 20 combinations to CSV
top_20_combinations = correlation_df.head(20)[
    ["combination", "n_genes_total", "pearson_r"]
]
top_20_combinations.columns = ["combination", "genes_total", "pearson_R"]
top_20_combinations["pearson_R"] = top_20_combinations["pearson_R"].round(3)
top_20_combinations.to_csv(
    "/Users/michael/Data/Luke_terrace_experiment/General_data/Junk_data/top_20_gene_combinations.csv",
    index=False,
)
print(
    "/Users/michael/Data/Luke_terrace_experiment/General_data/Junk_data/Saved top 20 combinations to 'top_20_gene_combinations.csv'"
)

/Users/michael/Data/Luke_terrace_experiment/General_data/Junk_data/Saved top 20 combinations to 'top_20_gene_combinations.csv'


In [26]:
# Get all Pseudomonas genera (all genera that start with "Pseudomonas")
pseudomonas_genera = [g for g in all_present_genus if g.startswith("Pseudomonas")]
print(f"Found {len(pseudomonas_genera)} Pseudomonas genera:")
print(pseudomonas_genera)

# Get total Pseudomonas abundance for each sample by summing all Pseudomonas genera
all_pseudomonas_data = genus_sum_w_tp[genus_sum_w_tp["Genus"].isin(pseudomonas_genera)]
total_pseudomonas_abundance = all_pseudomonas_data.groupby("Sample")["AbundR100"].sum()

print(
    f"\nTotal Pseudomonas abundance range: {total_pseudomonas_abundance.min():.2f} to {total_pseudomonas_abundance.max():.2f}"
)

# Get common samples between transcriptome and microbiome data
common_lic_ids = list(
    set(long_term_metadata["sampID"]) & set(total_pseudomonas_abundance.index)
)
common_filenames = long_term_metadata[
    long_term_metadata["sampID"].isin(common_lic_ids)
].index.tolist()
common_filenames = [f for f in common_filenames if f in long_term_transcriptome.index]

print(
    f"\nFound {len(common_filenames)} samples in common between transcriptome and microbiome data"
)

# Calculate correlation for each gene set combination
correlation_results_total_pseudo = []

for combo_name, gene_set in filtered_combinations.items():
    # Get genes that are actually in the transcriptome
    genes_in_data = list(set(gene_set) & set(long_term_transcriptome.columns))

    if len(genes_in_data) == 0:
        continue

    # Calculate mean expression for these genes in each sample
    mean_expression = long_term_transcriptome.loc[common_filenames, genes_in_data].mean(
        axis=1
    )

    # Get corresponding total Pseudomonas abundance
    lic_ids = long_term_metadata.loc[common_filenames, "sampID"]
    pseudo_abund = total_pseudomonas_abundance.loc[lic_ids].values

    # Calculate correlations
    pearson_corr, pearson_pval = pearsonr(mean_expression.values, pseudo_abund)
    spearman_corr, spearman_pval = spearmanr(mean_expression.values, pseudo_abund)

    correlation_results_total_pseudo.append(
        {
            "combination": combo_name,
            "n_genes_total": len(gene_set),
            "n_genes_in_data": len(genes_in_data),
            "pearson_r": pearson_corr,
            "pearson_pval": pearson_pval,
            "spearman_r": spearman_corr,
            "spearman_pval": spearman_pval,
        }
    )

# Convert to DataFrame and sort by absolute Pearson correlation
correlation_df_total_pseudo = pd.DataFrame(correlation_results_total_pseudo)
correlation_df_total_pseudo["abs_pearson"] = correlation_df_total_pseudo[
    "pearson_r"
].abs()
correlation_df_total_pseudo = correlation_df_total_pseudo.sort_values(
    "abs_pearson", ascending=False
)

print(f"\nAnalyzed {len(correlation_df_total_pseudo)} gene set combinations")
print("\nTop 20 combinations by absolute Pearson correlation with total Pseudomonas:")
print(correlation_df_total_pseudo.head(20).to_string())

Found 4 Pseudomonas genera:
['Pseudomonas_B_650453', 'Pseudomonas_E_647464', 'Pseudomonas_E_647626', 'Pseudomonas_M']

Total Pseudomonas abundance range: 0.00 to 44.40

Found 214 samples in common between transcriptome and microbiome data

Analyzed 8173 gene set combinations

Top 20 combinations by absolute Pearson correlation with total Pseudomonas:
                                                                 combination  n_genes_total  n_genes_in_data  pearson_r  pearson_pval  spearman_r  spearman_pval  abs_pearson
76                                              GO:0002237 OR GO:Luke Custom             65               65   0.173391      0.011056    0.212588       0.001763     0.173391
358                               GO:0002237 OR GO:0010421 OR GO:Luke Custom             67               67   0.173153      0.011169    0.212537       0.001768     0.173153
347                               GO:0034055 OR GO:0002237 OR GO:Luke Custom             66               66   0.173128      